In [1]:
# ============================================================================
# Greenblatt's Magic Formula Implementation
# Author - Jie Situ
# =============================================================================


import requests
from bs4 import BeautifulSoup
import pandas as pd

In [2]:
tickers = ["AXP","AAPL","BA","CAT","CVX","CSCO","DIS","DOW", "XOM",
           "HD","IBM","INTC","JNJ","KO","MCD","MMM","MRK","MSFT",
           "NKE","PFE","PG","TRV","UTX","UNH","VZ","V","WMT","WBA"]

#list of tickers whose financial data needs to be extracted
financial_dir = {}

In [3]:
for ticker in tickers:
    try:
    #getting balance sheet data from yahoo finance for the given ticker
        temp_dir = {}
        url = 'https://in.finance.yahoo.com/quote/'+ticker+'/balance-sheet?p='+ticker
        page = requests.get(url)
        page_content = page.content
        soup = BeautifulSoup(page_content,'html.parser')
        tabl = soup.find_all("div", {"class" : "M(0) Whs(n) BdEnd Bdc($seperatorColor) D(itb)"})
        for t in tabl:
            rows = t.find_all("div", {"class" : "rw-expnded"})
            for row in rows:
                temp_dir[row.get_text(separator='|').split("|")[0]]=row.get_text(separator='|').split("|")[1]
        
        #getting income statement data from yahoo finance for the given ticker
        url = 'https://in.finance.yahoo.com/quote/'+ticker+'/financials?p='+ticker
        page = requests.get(url)
        page_content = page.content
        soup = BeautifulSoup(page_content,'html.parser')
        tabl = soup.find_all("div", {"class" : "M(0) Whs(n) BdEnd Bdc($seperatorColor) D(itb)"})
        for t in tabl:
            rows = t.find_all("div", {"class" : "rw-expnded"})
            for row in rows:
                temp_dir[row.get_text(separator='|').split("|")[0]]=row.get_text(separator='|').split("|")[2]
        
        #getting cashflow statement data from yahoo finance for the given ticker
        url = 'https://in.finance.yahoo.com/quote/'+ticker+'/cash-flow?p='+ticker
        page = requests.get(url)
        page_content = page.content
        soup = BeautifulSoup(page_content,'html.parser')
        tabl = soup.find_all("div", {"class" : "M(0) Whs(n) BdEnd Bdc($seperatorColor) D(itb)"})
        for t in tabl:
            rows = t.find_all("div", {"class" : "rw-expnded"})
            for row in rows:
                temp_dir[row.get_text(separator='|').split("|")[0]]=row.get_text(separator='|').split("|")[2]
        
        #getting key statistics data from yahoo finance for the given ticker
        url = 'https://in.finance.yahoo.com/quote/'+ticker+'/key-statistics?p='+ticker
        page = requests.get(url)
        page_content = page.content
        soup = BeautifulSoup(page_content,'html.parser')
        #tabl = soup.findAll("table", {"class": "W(100%) Bdcl(c) "}) 
        tabl=soup.findAll("table")
        for t in tabl:
            rows = t.find_all("tr")
            for row in rows:
                if len(row.get_text(separator='|').split("|")[0:2])>0:
                    temp_dir[row.get_text(separator='|').split("|")[0]]=row.get_text(separator='|').split("|")[-1]    
        
        #combining all extracted information with the corresponding ticker
        financial_dir[ticker] = temp_dir
    except:
        print("Problem scraping data for ",ticker)


Problem scraping data for  KO


In [4]:
financial_dir['AAPL']

{'Assets': 'Current assets',
 'Current assets': 'Cash',
 'Cash': 'Cash and cash equivalents',
 'Cash and cash equivalents': '4,88,44,000',
 'Other short-term investments': '5,17,13,000',
 'Total cash': '94.05B',
 'Net receivables': '2,29,26,000',
 'Inventory': '-2,89,000',
 'Other current assets': '1,23,52,000',
 'Total current assets': '16,28,19,000',
 'Non-current assets': 'Property, plant and equipment',
 'Property, plant and equipment': 'Gross property, plant and equipment',
 'Gross property, plant and equipment': '9,59,57,000',
 'Accumulated depreciation': '-5,85,79,000',
 'Net property, plant and equipment': '3,73,78,000',
 'Equity and other investments': '10,53,41,000',
 'Goodwill': '-',
 'Intangible assets': '-',
 'Other long-term assets': '3,29,78,000',
 'Total non-current assets': '17,56,97,000',
 'Total assets': '33,85,16,000',
 "Liabilities and stockholders' equity": 'Liabilities',
 'Liabilities': 'Current liabilities',
 'Current liabilities': 'Current debt',
 'Current debt

In [5]:
#storing information in pandas dataframe
combined_financials = pd.DataFrame(financial_dir)
combined_financials.dropna(how='all',axis=1,inplace=True) #dropping columns with all NaN values
tickers = combined_financials.columns #updating the tickers list based on only those tickers whose values were successfully extracted


In [6]:
tickers

Index(['AXP', 'AAPL', 'BA', 'CAT', 'CVX', 'CSCO', 'DIS', 'DOW', 'XOM', 'HD',
       'IBM', 'INTC', 'JNJ', 'KO', 'MCD', 'MMM', 'MRK', 'MSFT', 'NKE', 'PFE',
       'PG', 'TRV', 'UTX', 'UNH', 'VZ', 'V', 'WMT', 'WBA'],
      dtype='object')

In [7]:
for ticker in tickers:
    combined_financials = combined_financials[~combined_financials[ticker].str.contains("[a-z]").fillna(False)]

combined_financials

AXP          AAPL  \
Total assets                            19,83,21,000  33,85,16,000   
Total liabilities                       17,52,50,000  24,80,28,000   
Common stock                                1,63,000   4,51,74,000   
Retained earnings                        1,38,71,000   4,58,98,000   
Accumulated other comprehensive income    -27,37,000     -5,84,000   
...                                              ...           ...   
Shares short                                     NaN           NaN   
Short ratio                                      NaN           NaN   
Short % of float                                 NaN           NaN   
Short % of shares outstanding                    NaN           NaN   
Shares short (prior month )                      NaN           NaN   

                                                  BA          CAT  \
Total assets                            13,36,25,000  7,84,53,000   
Total liabilities                       14,19,25,000  6,38,24,000   
Common stock                               50,61,000    59,35,000   
Retained earnings                        5,06,44,000  3,44,37,000   
Accumulated other comprehensive income  -1,61,53,000   -15,67,000   
...                                              ...          ...   
Shares short                                     NaN          NaN   
Short ratio                                      NaN          NaN   
Short % of float                                 NaN          NaN   
Short % of shares outstanding                    NaN          NaN   
Shares short (prior month )                      NaN          NaN   

                                                 CVX         CSCO  \
Total assets                            23,74,28,000  9,77,93,000   
Total liabilities                        9,22,20,000  6,42,22,000   
Common stock                               18,32,000  4,02,66,000   
Retained earnings                       17,49,45,000   -59,03,000   
Accumulated other comprehensive income    -52,30,000    -7,92,000   
...                                              ...          ...   
Shares short                                     NaN          NaN   
Short ratio                                      NaN          NaN   
Short % of float                                 NaN          NaN   
Short % of shares outstanding                    NaN          NaN   
Shares short (prior month )                      NaN          NaN   

                                                 DIS           DOW  \
Total assets                            19,39,84,000   6,05,24,000   
Total liabilities                       10,00,95,000   4,64,30,000   
Common stock                             5,39,07,000         8,000   
Retained earnings                        4,24,94,000   1,70,45,000   
Accumulated other comprehensive income    -66,17,000  -1,02,46,000   
...                                              ...           ...   
Shares short                                     NaN           NaN   
Short ratio                                      NaN           NaN   
Short % of float                                 NaN           NaN   
Short % of shares outstanding                    NaN           NaN   
Shares short (prior month )                      NaN           NaN   

                                                 XOM           HD  ...  \
Total assets                            36,25,97,000  5,12,36,000  ...   
Total liabilities                       16,36,59,000  5,43,52,000  ...   
Common stock                             1,56,37,000       89,000  ...   
Retained earnings                       42,13,41,000  5,17,29,000  ...   
Accumulated other comprehensive income  -1,94,93,000    -7,39,000  ...   
...                                              ...          ...  ...   
Shares short                                     NaN          NaN  ...   
Short ratio                                      NaN          NaN  ...   
Short % of float                           

In [8]:
# creating dataframe with relevant financial information for each stock using fundamental data
stats = ["EBITDA",
         "Depreciation & amortisation",
         "Market cap (intra-day)",
         "Net income available to common shareholders",
         "Net cash provided by operating activities",
         "Capital expenditure",
         "Total current assets",
         "Total current liabilities",
         "Net property, plant and equipment",
         "Total stockholders' equity",
         "Long-term debt",
         "Forward annual dividend yield"] # change as required

indx = ["EBITDA","D&A","MarketCap","NetIncome","CashFlowOps","Capex","CurrAsset",
        "CurrLiab","PPE","BookValue","TotDebt","DivYield"]
all_stats = {}


In [9]:
temp=combined_financials['AAPL']
temp

Total assets                              33,85,16,000
Total liabilities                         24,80,28,000
Common stock                               4,51,74,000
Retained earnings                          4,58,98,000
Accumulated other comprehensive income       -5,84,000
                                              ...     
Shares short                                       NaN
Short ratio                                        NaN
Short % of float                                   NaN
Short % of shares outstanding                      NaN
Shares short (prior month )                        NaN
Name: AAPL, Length: 136, dtype: object

In [10]:
ticker_stats=[]
ticker_stats.append(temp.loc['EBITDA'])
ticker_stats

['77.31B']

In [11]:
for ticker in tickers:
    temp = combined_financials[ticker]
    ticker_stats = []
    for stat in stats:
        ticker_stats.append(temp.loc[stat])
    all_stats[ticker] = ticker_stats


In [12]:
all_stats

{'AXP': ['N/A',
  '11,88,000',
  '88.33B',
  '66,31,000',
  '1,36,32,000',
  '-16,45,000',
  nan,
  nan,
  nan,
  '2,30,71,000',
  nan,
  '1.61%'],
 'AAPL': ['77.31B',
  '1,25,47,000',
  '1.44T',
  '5,52,56,000',
  '6,93,91,000',
  '-1,04,95,000',
  '16,28,19,000',
  '10,57,18,000',
  '3,73,78,000',
  '9,04,88,000',
  '9,18,07,000',
  '1.02%'],
 'BA': ['-2.48B',
  '22,71,000',
  '115.93B',
  '-6,36,000',
  '-24,46,000',
  '-19,61,000',
  '10,22,29,000',
  '9,73,12,000',
  '1,25,02,000',
  '-86,17,000',
  '1,98,04,000',
  'N/A'],
 'CAT': ['10B',
  '25,77,000',
  '73.13B',
  '60,93,000',
  '69,12,000',
  '-26,69,000',
  '3,91,93,000',
  '2,66,21,000',
  '1,29,04,000',
  '1,45,88,000',
  '2,61,53,000',
  '3.19%'],
 'CVX': ['28.56B',
  nan,
  '188.21B',
  '29,24,000',
  '2,73,14,000',
  '-1,41,16,000',
  '2,83,29,000',
  '2,65,30,000',
  '15,04,94,000',
  '14,42,13,000',
  '2,36,91,000',
  '5.36%'],
 'CSCO': ['16.18B',
  '18,97,000',
  '201.95B',
  '1,16,21,000',
  '1,58,31,000',
  '-9,09,

In [13]:
# cleansing of fundamental data imported in dataframe
all_stats_df = pd.DataFrame(all_stats,index=indx)
all_stats_df[tickers] = all_stats_df[tickers].replace({',': ''}, regex=True)
all_stats_df[tickers] = all_stats_df[tickers].replace({'M': 'E+03'}, regex=True)
all_stats_df[tickers] = all_stats_df[tickers].replace({'B': 'E+06'}, regex=True)
all_stats_df[tickers] = all_stats_df[tickers].replace({'T': 'E+09'}, regex=True)
all_stats_df[tickers] = all_stats_df[tickers].replace({'%': 'E-02'}, regex=True)
for ticker in all_stats_df.columns:
    all_stats_df[ticker] = pd.to_numeric(all_stats_df[ticker].values,errors='coerce')
all_stats_df.dropna(axis=1,inplace=True)
tickers = all_stats_df.columns

In [14]:
# calculating relevant financial metrics for each stock
transpose_df = all_stats_df.transpose()
final_stats_df = pd.DataFrame()
final_stats_df["EBIT"] = transpose_df["EBITDA"] - transpose_df["D&A"]
final_stats_df["TEV"] =  transpose_df["MarketCap"].fillna(0) \
                         +transpose_df["TotDebt"].fillna(0) \
                         -(transpose_df["CurrAsset"].fillna(0)-transpose_df["CurrLiab"].fillna(0))
final_stats_df["EarningYield"] =  final_stats_df["EBIT"]/final_stats_df["TEV"]
final_stats_df["FCFYield"] = (transpose_df["CashFlowOps"]-transpose_df["Capex"])/transpose_df["MarketCap"]
final_stats_df["ROC"]  = (transpose_df["EBITDA"] - transpose_df["D&A"])/(transpose_df["PPE"]+transpose_df["CurrAsset"]-transpose_df["CurrLiab"])
final_stats_df["BookToMkt"] = transpose_df["BookValue"]/transpose_df["MarketCap"]
final_stats_df["DivYield"] = transpose_df["DivYield"]

In [15]:
final_stats_df

EBIT           TEV  EarningYield  FCFYield       ROC  BookToMkt  \
AAPL  64763000.0  1.474706e+09      0.043916  0.055476  0.685475   0.062839   
CAT    7423000.0  8.671100e+07      0.085606  0.131013  0.291372   0.199480   
CSCO  14283000.0  2.003820e+08      0.071279  0.082892  0.758443   0.166234   
DOW    3572000.0  4.240900e+07      0.084227  0.242278  0.122312   0.415751   
HD    15584000.0  3.013850e+08      0.051708  0.059825  0.522953  -0.011366   
IBM    9971000.0  1.706430e+08      0.058432  0.150750  0.634126   0.177733   
INTC  25884000.0  2.887990e+08      0.089626  0.181183  0.402457   0.285071   
JNJ   21541000.0  4.055140e+08      0.053120  0.069307  0.798761   0.153146   
KO    10755000.0  2.449180e+08      0.043913  0.059405  2.515201   0.090026   
MCD    8622100.0  1.807812e+08      0.047694  0.071731  0.230796  -0.056005   
MMM    7167000.0  1.100590e+08      0.065120  0.091069  0.514132   0.104507   
MRK   15408000.0  2.251030e+08      0.068449  0.081457  0.758417   0.124775   
MSFT  52408000.0  1.380530e+09      0.037962  0.046556  0.349415   0.072063   
NKE    5140000.0  1.545250e+08      0.033263  0.043964  0.383496   0.056599   
PFE   14520000.0  2.403760e+08      0.060405  0.075940  1.533911   0.315841   
PG    16236000.0  3.208490e+08      0.050603  0.063457  1.182262   0.161105   
UNH   19210000.0  3.517060e+08      0.054619  0.069430 -1.839334   0.194813   
VZ    31328000.0  3.462570e+08      0.090476  0.228448  0.292201   0.256958   
V     15694000.0  4.476340e+08      0.035060  0.030881  1.531122   0.079104   
WMT   23203000.0  4.039480e+08      0.057441  0.104459  0.208914   0.216903   
WBA    3842000.0  5.794700e+07      0.066302  0.183409  0.599469   0.591051   

      DivYield  
AAPL    0.0102  
CAT     0.0319  
CSCO    0.0307  
DOW     0.0673  
HD      0.0241  
IBM     0.0506  
INTC    0.0210  
JNJ     0.0275  
KO      0.0342  
MCD     0.0259  
MMM     0.0362  
MRK     0.0299  
MSFT    0.0112  
NKE     0.0097  
PFE     0.0422  
PG      0.0273  
UNH     0.0168  
VZ      0.0430  
V       0.0062  
WMT     0.0177  
WBA     0.0414

In [16]:
################################Output Dataframes##############################

# finding value stocks based on Magic Formula
final_stats_val_df = final_stats_df.loc[tickers,:]
final_stats_val_df["CombRank"] = final_stats_val_df["EarningYield"].rank(ascending=False,na_option='bottom')+final_stats_val_df["ROC"].rank(ascending=False,na_option='bottom')
final_stats_val_df["MagicFormulaRank"] = final_stats_val_df["CombRank"].rank(method='first')
value_stocks = final_stats_val_df.sort_values("MagicFormulaRank").iloc[:,[2,4,8]]
print("------------------------------------------------")
print("Value stocks based on Greenblatt's Magic Formula")
print(value_stocks)

final_stats_val_df

------------------------------------------------
Value stocks based on Greenblatt's Magic Formula
      EarningYield       ROC  MagicFormulaRank
CSCO      0.071279  0.758443               1.0
PFE       0.060405  1.533911               2.0
MRK       0.068449  0.758417               3.0
INTC      0.089626  0.402457               4.0
VZ        0.090476  0.292201               5.0
WBA       0.066302  0.599469               6.0
JNJ       0.053120  0.798761               7.0
IBM       0.058432  0.634126               8.0
KO        0.043913  2.515201               9.0
PG        0.050603  1.182262              10.0
CAT       0.085606  0.291372              11.0
MMM       0.065120  0.514132              12.0
V         0.035060  1.531122              13.0
DOW       0.084227  0.122312              14.0
AAPL      0.043916  0.685475              15.0
HD        0.051708  0.522953              16.0
WMT       0.057441  0.208914              17.0
UNH       0.054619 -1.839334              18.0
MCD      

EBIT           TEV  EarningYield  FCFYield       ROC  BookToMkt  \
AAPL  64763000.0  1.474706e+09      0.043916  0.055476  0.685475   0.062839   
CAT    7423000.0  8.671100e+07      0.085606  0.131013  0.291372   0.199480   
CSCO  14283000.0  2.003820e+08      0.071279  0.082892  0.758443   0.166234   
DOW    3572000.0  4.240900e+07      0.084227  0.242278  0.122312   0.415751   
HD    15584000.0  3.013850e+08      0.051708  0.059825  0.522953  -0.011366   
IBM    9971000.0  1.706430e+08      0.058432  0.150750  0.634126   0.177733   
INTC  25884000.0  2.887990e+08      0.089626  0.181183  0.402457   0.285071   
JNJ   21541000.0  4.055140e+08      0.053120  0.069307  0.798761   0.153146   
KO    10755000.0  2.449180e+08      0.043913  0.059405  2.515201   0.090026   
MCD    8622100.0  1.807812e+08      0.047694  0.071731  0.230796  -0.056005   
MMM    7167000.0  1.100590e+08      0.065120  0.091069  0.514132   0.104507   
MRK   15408000.0  2.251030e+08      0.068449  0.081457  0.758417   0.124775   
MSFT  52408000.0  1.380530e+09      0.037962  0.046556  0.349415   0.072063   
NKE    5140000.0  1.545250e+08      0.033263  0.043964  0.383496   0.056599   
PFE   14520000.0  2.403760e+08      0.060405  0.075940  1.533911   0.315841   
PG    16236000.0  3.208490e+08      0.050603  0.063457  1.182262   0.161105   
UNH   19210000.0  3.517060e+08      0.054619  0.069430 -1.839334   0.194813   
VZ    31328000.0  3.462570e+08      0.090476  0.228448  0.292201   0.256958   
V     15694000.0  4.476340e+08      0.035060  0.030881  1.531122   0.079104   
WMT   23203000.0  4.039480e+08      0.057441  0.104459  0.208914   0.216903   
WBA    3842000.0  5.794700e+07      0.066302  0.183409  0.599469   0.591051   

      DivYield  CombRank  MagicFormulaRank  
AAPL    0.0102      25.0              15.0  
CAT     0.0319      20.0              11.0  
CSCO    0.0307      11.0               1.0  
DOW     0.0673      24.0              14.0  
HD      0.0241      25.0              16.0  
IBM     0.0506      19.0               8.0  
INTC    0.0210      15.0               4.0  
JNJ     0.0275      18.0               7.0  
KO      0.0342      19.0               9.0  
MCD     0.0259      34.0              19.0  
MMM     0.0362      20.0              12.0  
MRK     0.0299      13.0               3.0  
MSFT    0.0112      34.0              20.0  
NKE     0.0097      35.0              21.0  
PFE     0.0422      11.0               2.0  
PG      0.0273      19.0              10.0  
UNH     0.0168      33.0              18.0  
VZ      0.0430      17.0               5.0  
V       0.0062      23.0              13.0  
WMT     0.0177      30.0              17.0  
WBA     0.0414      17.0               6.0

In [17]:
# finding highest dividend yield stocks
high_dividend_stocks = final_stats_df.sort_values("DivYield",ascending=False).iloc[:,6]
print("------------------------------------------------")
print("Highest dividend paying stocks")
print(high_dividend_stocks)

------------------------------------------------
Highest dividend paying stocks
DOW     0.0673
IBM     0.0506
VZ      0.0430
PFE     0.0422
WBA     0.0414
MMM     0.0362
KO      0.0342
CAT     0.0319
CSCO    0.0307
MRK     0.0299
JNJ     0.0275
PG      0.0273
MCD     0.0259
HD      0.0241
INTC    0.0210
WMT     0.0177
UNH     0.0168
MSFT    0.0112
AAPL    0.0102
NKE     0.0097
V       0.0062
Name: DivYield, dtype: float64


In [18]:
# # Magic Formula & Dividend yield combined
final_stats_df["CombRank"] = final_stats_df["EarningYield"].rank(ascending=False,method='first') \
                              +final_stats_df["ROC"].rank(ascending=False,method='first')  \
                              +final_stats_df["DivYield"].rank(ascending=False,method='first')
final_stats_df["CombinedRank"] = final_stats_df["CombRank"].rank(method='first')
value_high_div_stocks = final_stats_df.sort_values("CombinedRank").iloc[:,[2,4,6,8]]
print("------------------------------------------------")
print("Magic Formula and Dividend Yield combined")
print(value_high_div_stocks)


------------------------------------------------
Magic Formula and Dividend Yield combined
      EarningYield       ROC  DivYield  CombinedRank
PFE       0.060405  1.533911    0.0422           1.0
CSCO      0.071279  0.758443    0.0307           2.0
VZ        0.090476  0.292201    0.0430           3.0
IBM       0.058432  0.634126    0.0506           4.0
WBA       0.066302  0.599469    0.0414           5.0
MRK       0.068449  0.758417    0.0299           6.0
DOW       0.084227  0.122312    0.0673           7.0
KO        0.043913  2.515201    0.0342           8.0
MMM       0.065120  0.514132    0.0362           9.0
CAT       0.085606  0.291372    0.0319          10.0
JNJ       0.053120  0.798761    0.0275          11.0
INTC      0.089626  0.402457    0.0210          12.0
PG        0.050603  1.182262    0.0273          13.0
HD        0.051708  0.522953    0.0241          14.0
AAPL      0.043916  0.685475    0.0102          15.0
V         0.035060  1.531122    0.0062          16.0
WMT     

In [19]:
url = 'https://in.finance.yahoo.com/quote/AAPL/key-statistics?p=AAPL'
page = requests.get(url)
page_content = page.content
soup = BeautifulSoup(page_content,'html.parser')
#tabl = soup.findAll("table", {"class": "W(100%) Bdcl(c) "}) # 
tabl=soup.findAll("table") 
for t in tabl:
    rows = t.find_all("tr")
    for row in rows:
        if len(row.get_text(separator='|').split("|")[0:2])>0:
            temp_dir[row.get_text(separator='|').split("|")[0]]=row.get_text(separator='|').split("|")[-1]    
        

In [20]:
r=tabl[0].find_all('tr')
r[0].get_text(separator='|').split("|")

['Market cap (intra-day)', ' ', '5', '1.44T']